# Process and plots

This notebook performs the preprocessing of the raw data and combine them all into a single DataFrame to easy further exploration and processing.  
It contains the function calls that produce all the plots shown in the paper and the data visualization application references below:

> **Synchronous transmissions on Bluetooth 5 and IEEE 802.15.4 - A replication study**  
Romain Jacob, Anna-Brit Schaper, Andreas Biri, Reto da Forno, Lothar Thiele   
[CPS-IoTBench'20](https://cpsbench20.ethz.ch/)  
[ [Direct link](https://openreview.net/forum?id=BSZPNEUHiS2) ]
[ [Data Visualization](http://explore-st-data.ethz.ch/) ]

In [2]:
import os
from pathlib import Path

import pandas as pd
import numpy as np

from src.preprocess import parse_all_data, clean_raw_data, computeTimeDeltaTraces, computePowerDeltaTraces

import plotly.graph_objects as go
import plotly.io as pio
pio.templates.default = "none"

import src.colors as colors
from src.helpers import Modes, Parameters
from src.stats import ThompsonCI_twosided
from src.plots import prr_f_TimeDelta, prr_f_PowerDelta, prr_3d, prr_matrix_plot

In [3]:
##########
# Plot settings
##########

# Set to False to view larger versions of the plots
# Set to True  to reproduce the exact plots from the paper
PaperPlot = True

# Select the different output format settings
if PaperPlot:
    output_format = 'paper'
else:
    output_format = 'online'

if output_format == 'online':
    font_size_px = 14
    linewidth_px = 512
    landscapewidth_px = 654
    plot_path = None

if output_format == 'paper':
    font_size_pt = 6
    offset = 5 # to compensate for the rounding of unit conversions
    linewidth_pt = 241 - offset  
    landscapewidth_pt = 506 - offset
    
    # 1pt = 1.333px
    font_size_px = int(font_size_pt*1.333)+1
    linewidth_px = int(linewidth_pt*1.333)+1
    landscapewidth_px = int(landscapewidth_pt*1.333)+1

    plot_path = Path('plots_cps-iotbench')
    
# Create plot directory if don't exist
if (plot_path is not None) and (not os.path.exists(plot_path)):
    os.mkdir(plot_path)

In [4]:
# Clean up and bug correction of the initial raw data
clean_raw_data()

In [33]:
# Load data
df = parse_all_data()
DataPath = Path('data_preprocessed')
display(df)

Processed data retrieved.


LocalExpCount  TxPowerA  TxPowerB  Mode  TimeDelta  RxCount  \
GlobalExpCount                                                                
0                           0         8        -8     0       -140       20   
1                           1         8        -8     0       -120       20   
2                           2         8        -8     0       -100       20   
3                           3         8        -8     0        -90       20   
4                           4         8        -8     0        -80       20   
...                       ...       ...       ...   ...        ...      ...   
138595                   5895         8         8     4         80       19   
138596                   5896         8         8     4         90       20   
138597                   5897         8         8     4        100       20   
138598                   5898         8         8     4        120       20   
138599                   5899         8         8     4        140       17   

                TxCount  RssiA  RssiB    PRR  PowerDelta             DateTime  \
GlobalExpCount                                                                  
0                    20  -60.0    NaN  100.0         NaN  2019-09-06 11:16:09   
1                    20  -60.0    NaN  100.0         NaN  2019-09-06 11:16:09   
2                    20  -60.0    NaN  100.0         NaN  2019-09-06 11:16:09   
3                    20  -60.0    NaN  100.0         NaN  2019-09-06 11:16:09   
4                    20  -60.0    NaN  100.0         NaN  2019-09-06 11:16:09   
...                 ...    ...    ...    ...         ...                  ...   
138595               20  -61.0  -55.0   95.0         6.0  2019-10-04 13:55:00   
138596               20  -61.0  -55.0  100.0         6.0  2019-10-04 13:55:00   
138597               20  -61.0  -55.0  100.0         6.0  2019-10-04 13:55:00   
138598               20  -61.0  -55.0  100.0         6.0  2019-10-04 13:55:00   
138599               20  -61.0  -55.0   85.0         6.0  2019-10-04 13:55:00   

                SamePayload TransPair  
GlobalExpCount                         
0                         0         A  
1                         0         A  
2                         0         A  
3                         0         A  
4                         0         A  
...                     ...       ...  
138595                    1         B  
138596                    1         B  
138597                    1         B  
138598                    1         B  
138599                    1         B  

[138600 rows x 14 columns]

In [11]:
plot_name = 'prr_matrix.pdf'

# Adjust the plot size    
if output_format == 'paper':
    custom_layout = dict(
        font = {"size":font_size_px},
        margin = dict(l=100, r=10, t=30, b=40),
        width = 0.8*landscapewidth_px,        
        xaxis = {'tickvals':[-16,-8,8,16]}
    )
else: 
    custom_layout = None
    
figure = prr_matrix_plot(
    df,
    DataPath,
    PowerDeltaList = [0,2,4,6,8,10],
    custom_layout = custom_layout,
    SamePayload=1,
    showMarkers=False,
    )
figure.update_layout(custom_layout)
figure.show()
# figure.write_image(str(plot_path / plot_name))

In [32]:
if output_format == 'paper':
    custom_layout = dict(
        font = {"size":font_size_px},
        margin = dict(l=100, r=10, t=30, b=40),
        width = 0.8*landscapewidth_px,        
        xaxis = {'tickvals':[-16,-8,8,16]}
    )
else: 
    custom_layout = None
    
plot_name = 'prr_matrix_DiffPayload.pdf'
figure = prr_matrix_plot(
    df,
    DataPath,
    PowerDeltaList = [0,2,4,6,8,9],
    custom_layout = custom_layout,
    SamePayload=0
    )
figure.update_layout(custom_layout)
figure.show()
figure.write_image(str(plot_path / plot_name))

In [13]:

ModeList = [i for i in Modes]

# Adjust the plot size    
if output_format == 'paper':
    custom_layout = dict(
        font = {"size":font_size_px},
        margin = dict(l=30, r=5, t=25, b=25),
        xaxis = {'tickvals':[-16,-8,0,8,16]},
        width = 0.5*landscapewidth_px,
        height = 135,
        title = '',
        showlegend = False
    )
else: 
    custom_layout = None
    
# for i in [ModeList[0]]:
for i in Modes:
    
    # With same payload
    plot_name = 'CIdelayBound_%s.pdf' % i
    figure = prr_f_TimeDelta(
        df,
        PowerDelta=0,
        SamePayload=1,
        TransPair='all',
        ModesToShow=[i],
        DataPath=DataPath,
        showMarkers=True,
        showCI=True,
        showTimeThreshold=True
        )
    figure.update_layout(custom_layout)
    figure.show()
    figure.write_image(str(plot_path / plot_name))
    
    # With different payload
    plot_name = 'CIdelayBound_%s_DiffPayload.pdf' % i
    figure = prr_f_TimeDelta(
        df,
        PowerDelta=0,
        SamePayload=0,
        TransPair='all',
        ModesToShow=[i],
        DataPath=DataPath,
        showMarkers=True,
        showCI=True,
        showTimeThreshold=True
        )
    figure.update_layout(custom_layout)
    figure.show()
    figure.write_image(str(plot_path / plot_name))

In [15]:
ModeList = [i for i in Modes]

# Adjust the plot size    
if output_format == 'paper':
    custom_layout = dict(
        font = {"size":font_size_px},
        margin = dict(l=30, r=5, t=0, b=25),
        width = 0.4*landscapewidth_px,
        height = 150,
        title = '',
        showlegend = False,
        xaxis=dict(range=[-10,10])
    )
else: 
    custom_layout = None
        
# With same payload
plot_name = 'Power_SamePayload.pdf'
figure = prr_f_PowerDelta(
    df,
    TimeDelta=0,
    SamePayload=1,
    TransPair='all',
    ModesToShow=ModeList,
    DataPath=DataPath,
    showMarkers=False,
    showCI=True,
    )
figure.update_layout(custom_layout)
figure.show()
figure.write_image(str(plot_path / plot_name))

# With different payload
plot_name = 'Power_DiffPayload.pdf'
figure = prr_f_PowerDelta(
    df,
    TimeDelta=0,
    SamePayload=0,
    TransPair='all',
    ModesToShow=ModeList,
    DataPath=DataPath,
    showMarkers=False,
    showCI=True,
    )
figure.update_layout(custom_layout)
figure.show()
figure.write_image(str(plot_path / plot_name))

# "Legend only" plot
from src.plots import CI_opacity
plot_name = 'legend.pdf'
figure = go.Figure()
for mode in Modes:
    figure.add_trace(
        dict(
            x=[np.nan],
            y=[np.nan],
            mode='lines',
            marker={'color':Modes[mode]['color']},
            name=Modes[mode]['label'],
            hoverinfo='skip',
        )
    )

figure.add_trace(
    dict(
        x=[np.nan],
        y=[np.nan],
        mode='lines',
        line={
            'color':'grey',
            'width':0
        },
        name='75% conf.<br>interval',
        fill='toself',
        opacity=CI_opacity,
    )
)
layout = dict(
    font = {"size":font_size_px},
    margin = dict(l=0, r=0, t=0, b=0,),
    width = 0.13*landscapewidth_px,
    height = 120,
    legend = dict(
        orientation = 'v',
        xanchor = 'center',
        yanchor = 'middle',
        x = 0.5,
        y = 0.5
        )
    )
figure.update_layout(layout)
figure.show()
figure.write_image(str(plot_path / plot_name))

In [27]:
# Compute (or retrieve) all preprocessed data
df = parse_all_data(force_computation='')

# Parameters
PowerDelta = 0
TimeDelta = 0
SamePayload = 1
TransPair = "all"
showMarkers = True
showCI = True
ModesToShow = [mode for mode in Modes]

TimeDelta_plot = prr_f_TimeDelta(
    df,
    PowerDelta,
    SamePayload,
    TransPair,
    ModesToShow,
    showMarkers = showMarkers,
    showCI = showCI
    )
TimeDelta_plot.show()

PowerDelta_plot = prr_f_PowerDelta(
    df,
    TimeDelta,
    SamePayload,
    TransPair,
    ModesToShow,
    showMarkers = showMarkers,
    showCI = showCI)
PowerDelta_plot.show()

threeD_plot = prr_3d(
    df,
    SamePayload,
    TransPair,
    ModesToShow)

threeD_plot.show()

Processed data retrieved.


In [32]:
##########
# Example 
# -> filtering for a specific part of the dataset
##########

# Compute (or retrieve) all preprocessed data
df = parse_all_data()
data_path = Path('data_preprocessed')

PowerDelta,SamePayload,TransPair = 9, 1, "B"

filter = (
#     (df['DateTime'] == "2019-10-04 13:55:00") & 
    (df['TransPair'] == "B") & 
    (df['SamePayload'] == 1) & 
    (df["PowerDelta"] == 9)  
)
filtered_df = df.where(filter).dropna()
# display(filtered_df)

Processed data retrieved.
